In [1]:
import pandas as pd
import math
from pandas_datareader import data, wb
import numpy as np
import datetime
import seaborn as sns
import matplotlib.pyplot as plt
import matplotlib.dates as mdates
from matplotlib.widgets import TextBox
!pip install altair
import altair as alt
!pip install bar_chart_race
import bar_chart_race as bcr

In [2]:
from google.colab import drive

drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [3]:
df = pd.read_excel('/content/drive/MyDrive/Colab Notebooks/EMVOLIA.xlsx')
df.head()

Date Companies  Close_Price
0 2020-07-13    PFIZER    33.406071
1 2020-07-14    PFIZER    33.425049
2 2020-07-15    PFIZER    33.889942
3 2020-07-16    PFIZER    33.776093
4 2020-07-17    PFIZER    34.392788

In [4]:
df["Month"] = df.Date.dt.month

In [5]:
#Η εξέλιξη των εταιριών στο χρηματιστήριο 
alt.Chart(df, title="Examined Period: August 2020 - June 2021").mark_line().encode(
   x="Date",
   y="Close_Price",
   color="Companies"
).properties(
   height=300, width=500
)

alt.Chart(...)

In [6]:
#Η εξέλιξη των εταιριών στο χρηματιστήριο (animated)
hover = alt.selection(
   type="single", on="mouseover", fields=["Companies"], nearest=True
)
# line plot
lineplot = alt.Chart(df, title="Examined Period: August 2020 - June 2021").mark_line().encode(
   x="Date:T",
   y="Close_Price:Q",
   color="Companies:N",
)
# nearest point
point = lineplot.mark_circle().encode(
   opacity=alt.value(0)
).add_selection(hover)
# highlight
singleline = lineplot.mark_line().encode(
   size=alt.condition(~hover, alt.value(0.5), alt.value(3))
)
point + singleline

alt.LayerChart(...)

In [7]:
## Ας δούμε κάποιες γενικές πληροφορίες σχετικά με  τα συνολικά κρούσματα (interactive plots)

In [8]:
total = pd.read_excel('/content/drive/MyDrive/Colab Notebooks/Covid_data (1).xlsx')
total.head()

iso_code continent  ... life_expectancy human_development_index
0      AFG      Asia  ...           64.83                   0.511
1      AFG      Asia  ...           64.83                   0.511
2      AFG      Asia  ...           64.83                   0.511
3      AFG      Asia  ...           64.83                   0.511
4      AFG      Asia  ...           64.83                   0.511

[5 rows x 59 columns]

In [9]:
total2=total[['date','continent','location','total_cases', 'new_cases', 'total_deaths','life_expectancy']]
total2

date continent  ... total_deaths  life_expectancy
0      2020-02-24      Asia  ...          NaN            64.83
1      2020-02-25      Asia  ...          NaN            64.83
2      2020-02-26      Asia  ...          NaN            64.83
3      2020-02-27      Asia  ...          NaN            64.83
4      2020-02-28      Asia  ...          NaN            64.83
...           ...       ...  ...          ...              ...
101539 2021-07-06    Africa  ...       1939.0            61.49
101540 2021-07-07    Africa  ...       1973.0            61.49
101541 2021-07-08    Africa  ...       2029.0            61.49
101542 2021-07-09    Africa  ...       2084.0            61.49
101543 2021-07-10    Africa  ...       2126.0            61.49

[101544 rows x 7 columns]

In [10]:
# remove blanks from continent and replace NaN with 0
total2.dropna(subset=['continent'], inplace=True)
total2=total2.fillna(0)
total2

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


date continent  ... total_deaths  life_expectancy
0      2020-02-24      Asia  ...          0.0            64.83
1      2020-02-25      Asia  ...          0.0            64.83
2      2020-02-26      Asia  ...          0.0            64.83
3      2020-02-27      Asia  ...          0.0            64.83
4      2020-02-28      Asia  ...          0.0            64.83
...           ...       ...  ...          ...              ...
101539 2021-07-06    Africa  ...       1939.0            61.49
101540 2021-07-07    Africa  ...       1973.0            61.49
101541 2021-07-08    Africa  ...       2029.0            61.49
101542 2021-07-09    Africa  ...       2084.0            61.49
101543 2021-07-10    Africa  ...       2126.0            61.49

[96794 rows x 7 columns]

In [11]:
total2.dtypes

date               datetime64[ns]
continent                  object
location                   object
total_cases               float64
new_cases                 float64
total_deaths              float64
life_expectancy           float64
dtype: object

In [12]:
total2['year'] = pd.DatetimeIndex(total2['date']).year
total2['month'] = pd.DatetimeIndex(total2['date']).month
total2['day'] = pd.DatetimeIndex(total2['date']).day
total2

date continent     location  ...  year  month  day
0      2020-02-24      Asia  Afghanistan  ...  2020      2   24
1      2020-02-25      Asia  Afghanistan  ...  2020      2   25
2      2020-02-26      Asia  Afghanistan  ...  2020      2   26
3      2020-02-27      Asia  Afghanistan  ...  2020      2   27
4      2020-02-28      Asia  Afghanistan  ...  2020      2   28
...           ...       ...          ...  ...   ...    ...  ...
101539 2021-07-06    Africa     Zimbabwe  ...  2021      7    6
101540 2021-07-07    Africa     Zimbabwe  ...  2021      7    7
101541 2021-07-08    Africa     Zimbabwe  ...  2021      7    8
101542 2021-07-09    Africa     Zimbabwe  ...  2021      7    9
101543 2021-07-10    Africa     Zimbabwe  ...  2021      7   10

[96794 rows x 10 columns]

In [13]:
# Διαλέγω την ημερομηνία που είναι και στα πρώτα γραφήματα
total3=total2[total2["date"] > '2020-07-13']
total3

date continent     location  ...  year  month  day
141    2020-07-14      Asia  Afghanistan  ...  2020      7   14
142    2020-07-15      Asia  Afghanistan  ...  2020      7   15
143    2020-07-16      Asia  Afghanistan  ...  2020      7   16
144    2020-07-17      Asia  Afghanistan  ...  2020      7   17
145    2020-07-18      Asia  Afghanistan  ...  2020      7   18
...           ...       ...          ...  ...   ...    ...  ...
101539 2021-07-06    Africa     Zimbabwe  ...  2021      7    6
101540 2021-07-07    Africa     Zimbabwe  ...  2021      7    7
101541 2021-07-08    Africa     Zimbabwe  ...  2021      7    8
101542 2021-07-09    Africa     Zimbabwe  ...  2021      7    9
101543 2021-07-10    Africa     Zimbabwe  ...  2021      7   10

[71767 rows x 10 columns]

In [14]:
total3[['location','new_cases']].groupby('location').sum().sort_values(by= 'new_cases', ascending=False).head(10)

new_cases
location                  
United States   30477481.0
India           29930470.0
Brazil          17184036.0
France           6007306.0
Russia           4956260.0
United Kingdom   4816089.0
Argentina        4535833.0
Turkey           4427868.0
Colombia         4317345.0
Italy            4026655.0

In [15]:
import plotly.express as px

In [16]:
# Συνολικά κρούμστα ανα continent
fig = px.bar(total3, x="date", y="total_cases", color='continent', height=600, width=900)
fig.update_layout(title="Total Cases per Continent", xaxis_title="Date", yaxis_title="Total Cases")
fig.show()

In [17]:
# Συνολικά κρούσματα (Top-10)

filter_list = ['India',	'United States','	Brazil','	France','	Turkey', 'Argentina',	'Colombia', 'United Kingdom', 'Russia', 'Italy'	]
total4=total3[total3.location.isin(filter_list)]
fig = px.line(total4, x="date", y="total_cases", color='location', height=600, width=900)
fig.update_layout(title="Total Cases per Country (Top 10)", xaxis_title="Date", yaxis_title="Total Cases")
fig.show()

In [18]:
life=total[['date','continent','location','total_cases','total_deaths','life_expectancy','population_density']]
life

date continent  ... life_expectancy  population_density
0      2020-02-24      Asia  ...           64.83              54.422
1      2020-02-25      Asia  ...           64.83              54.422
2      2020-02-26      Asia  ...           64.83              54.422
3      2020-02-27      Asia  ...           64.83              54.422
4      2020-02-28      Asia  ...           64.83              54.422
...           ...       ...  ...             ...                 ...
101539 2021-07-06    Africa  ...           61.49              42.729
101540 2021-07-07    Africa  ...           61.49              42.729
101541 2021-07-08    Africa  ...           61.49              42.729
101542 2021-07-09    Africa  ...           61.49              42.729
101543 2021-07-10    Africa  ...           61.49              42.729

[101544 rows x 7 columns]

In [19]:
life.dropna(subset=['continent'], inplace=True)
life=life.fillna(0)
life['year'] = pd.DatetimeIndex(life['date']).year
life['month'] = pd.DatetimeIndex(life['date']).month
life=life[life["year"] == 2021]
life

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



date continent     location  ...  population_density  year  month
312    2021-01-01      Asia  Afghanistan  ...              54.422  2021      1
313    2021-01-02      Asia  Afghanistan  ...              54.422  2021      1
314    2021-01-03      Asia  Afghanistan  ...              54.422  2021      1
315    2021-01-04      Asia  Afghanistan  ...              54.422  2021      1
316    2021-01-05      Asia  Afghanistan  ...              54.422  2021      1
...           ...       ...          ...  ...                 ...   ...    ...
101539 2021-07-06    Africa     Zimbabwe  ...              42.729  2021      7
101540 2021-07-07    Africa     Zimbabwe  ...              42.729  2021      7
101541 2021-07-08    Africa     Zimbabwe  ...              42.729  2021      7
101542 2021-07-09    Africa     Zimbabwe  ...              42.729  2021      7
101543 2021-07-10    Africa     Zimbabwe  ...              42.729  2021      7

[39713 rows x 9 columns]

In [20]:
life1 = life
px.scatter(life1, x="total_deaths", y="life_expectancy", animation_frame="month", animation_group="location",
           size="total_cases", color="continent", hover_name="location", 
           title="Total Deaths in relation with Life Expectancy and total number of confirmed cases for 2021",
           log_x=True, size_max=100, range_x=[10,10000000], range_y=[30,100])